In [1]:
!pip install requests pandas folium geopandas

In [2]:
!pip install streamlit

In [3]:
import requests
import pandas as pd

def fetch_data(city):
    # API endpoint
    endpoint = "http://tour-pedia.org/api/getPlaces"
    categories = ['accommodation', 'attraction', 'restaurant', 'poi']
    all_data = pd.DataFrame()
    
    for category in categories:
        # Set parameters for the API request
        params = {
            'location': city,   
            'category': category  
        }
        response = requests.get(endpoint, params=params)
        
        # Check if the request was successful
        print(f"Fetching {category} data for {city}... Status Code: {response.status_code}")
        if response.status_code == 200:
            category_data = pd.DataFrame(response.json())
            if not category_data.empty:
                print(f"Fetched {len(category_data)} records for {category} in {city}.")
            else:
                print(f"No data found for {category} in {city}.")
                
            all_data = pd.concat([all_data, category_data], ignore_index=True)
        else:
            print(f"Error fetching {category} data for {city}: {response.status_code}")
    
    if all_data.empty:
        print(f"No data available for {city}.")
        
    return all_data

cities = ['Amsterdam', 'Barcelona', 'Berlin', 'Dubai', 'London', 'Paris', 'Rome', 'Tuscany']
data = {city: fetch_data(city) for city in cities}

for city, df in data.items():
    print(f"\nData for {city}:")
    if not df.empty:
        print(df.head())
    else:
        print(f"No data retrieved for {city}.")

Fetching accommodation data for Amsterdam... Status Code: 200
Fetched 1393 records for accommodation in Amsterdam.
Fetching attraction data for Amsterdam... Status Code: 200
Fetched 3185 records for attraction in Amsterdam.
Fetching restaurant data for Amsterdam... Status Code: 200
Fetched 5241 records for restaurant in Amsterdam.
Fetching poi data for Amsterdam... Status Code: 200
Fetched 10441 records for poi in Amsterdam.
Fetching accommodation data for Barcelona... Status Code: 200
Fetched 2450 records for accommodation in Barcelona.
Fetching attraction data for Barcelona... Status Code: 200
Fetched 2390 records for attraction in Barcelona.
Fetching restaurant data for Barcelona... Status Code: 200
Fetched 8411 records for restaurant in Barcelona.
Fetching poi data for Barcelona... Status Code: 200
Fetched 10778 records for poi in Barcelona.
Fetching accommodation data for Berlin... Status Code: 200
Fetched 2887 records for accommodation in Berlin.
Fetching attraction data for Berl

# Fixed Final Version

In [17]:
import folium
from folium.plugins import HeatMap
from IPython.display import display

category_colors = {
    'restaurant': 'orange',
    'attraction': 'purple',
    'accommodation': 'green',
    'point of interest': 'black',  
}

# Creates a dynamic map with heatmap and markers
def create_map(city, df):

    # Cleaning / verifying fetched data
    if 'lat' not in df.columns or 'lng' not in df.columns:
        print(f"Error: Missing latitude or longitude data for {city}.")
        return None
    df = df.dropna(subset=['lat', 'lng', 'polarity'])
    if df.empty:
        print(f"No valid data available for creating a map of {city}.")
        return None

    # Sort the DataFrame by polarity and select the top 300 rows
    df = df.sort_values(by='polarity', ascending=False).head(300)

    # Create the base map centered around the city using average latitude and longitude
    avg_lat = df['lat'].mean()
    avg_lon = df['lng'].mean()
    map_city = folium.Map(location=[avg_lat, avg_lon], zoom_start=13)

    # Create a FeatureGroup for the heatmap to allow naming it "Heatmap"
    heatmap_group = folium.FeatureGroup(name="Heatmap")
    heat_data = [[row['lat'], row['lng'], row['polarity']] for index, row in df.iterrows()]
    HeatMap(heat_data, radius=15).add_to(heatmap_group)
    heatmap_group.add_to(map_city)

    # Create a feature group for markers to allow toggling
    marker_group = folium.FeatureGroup(name="Markers", show=True)

    # Add markers to the feature group with color coding based on category
    for index, row in df.iterrows():
        marker_color = category_colors.get(row['category'].lower().strip(), 'black')
        
        folium.Marker(
            location=[row['lat'], row['lng']],
            popup=folium.Popup(
                html=(
                    f"<b>Name:</b> {row['name']}<br>"
                    f"<b>Category:</b> {row['category']}<br>"
                    f"<b>Address:</b> {row['address']}<br>"
                    f"<b>Number of Reviews:</b> {row['numReviews']}<br>"
                    f"<b>Polarity:</b> {row['polarity']}"
                ),
                max_width=300  
            ),
            icon=folium.Icon(color=marker_color, icon='info-sign')
        ).add_to(marker_group)

    marker_group.add_to(map_city)
    folium.LayerControl(collapsed=False).add_to(map_city)

    legend_html = '''
     <div style="position: fixed; 
                 bottom: 180px; left: 50px; width: 250px; height: 200px; 
                 border:2px solid grey; z-index:9999; font-size:14px;
                 background-color:white; padding: 10px;">
     <b>Heatmap Intensity</b><br>
     <i style="background: blue; width: 20px; height: 20px; display: inline-block;"></i> Lowest Density<br>
     <i style="background: lightblue; width: 20px; height: 20px; display: inline-block;"></i> Low Density<br>
     <i style="background: green; width: 20px; height: 20px; display: inline-block;"></i> Moderate Density<br>
     <i style="background: yellow; width: 20px; height: 20px; display: inline-block;"></i> High Density<br>
     <i style="background: orange; width: 20px; height: 20px; display: inline-block;"></i> Higher Density<br>
     <i style="background: red; width: 20px; height: 20px; display: inline-block;"></i> Highest Density<br>
     </div>
     '''
    map_city.get_root().html.add_child(folium.Element(legend_html))

    marker_legend_html = '''
     <div style="position: fixed; 
                 bottom: 20px; left: 50px; width: 250px; height: 150px; 
                 border:2px solid grey; z-index:9999; font-size:14px;
                 background-color:white; padding: 10px;">
     <b>Marker Colors</b><br>
     <i style="background: orange; width: 20px; height: 20px; display: inline-block;"></i> Restaurant<br>
     <i style="background: purple; width: 20px; height: 20px; display: inline-block;"></i> Attraction<br>
     <i style="background: green; width: 20px; height: 20px; display: inline-block;"></i> Accommodation<br>
     <i style="background: black; width: 20px; height: 20px; display: inline-block;"></i> Point of Interest<br>
     </div>
     '''
    map_city.get_root().html.add_child(folium.Element(marker_legend_html))

    # Comment out or not depending on if I want to display map in Jupyter notebook
    display(map_city)  

    # Save the map as an HTML file
    map_city.save(f"{city}_mapfinal.html")
    print(f"Map for {city} has been created and saved as {city}_mapfinal.html.")
    return map_city

for city, df in data.items():
    print(f"Creating and displaying map for {city} with top 300 locations...")
    if not df.empty:
        create_map(city, df)  
    else:
        print(f"No data available for {city}.")

Creating and displaying map for Amsterdam with top 300 locations...


Map for Amsterdam has been created and saved as Amsterdam_mapfinal.html.
Creating and displaying map for Barcelona with top 300 locations...


Map for Barcelona has been created and saved as Barcelona_mapfinal.html.
Creating and displaying map for Berlin with top 300 locations...


Map for Berlin has been created and saved as Berlin_mapfinal.html.
Creating and displaying map for Dubai with top 300 locations...


Map for Dubai has been created and saved as Dubai_mapfinal.html.
Creating and displaying map for London with top 300 locations...


Map for London has been created and saved as London_mapfinal.html.
Creating and displaying map for Paris with top 300 locations...


Map for Paris has been created and saved as Paris_mapfinal.html.
Creating and displaying map for Rome with top 300 locations...


Map for Rome has been created and saved as Rome_mapfinal.html.
Creating and displaying map for Tuscany with top 300 locations...


Map for Tuscany has been created and saved as Tuscany_mapfinal.html.


# One city (Berlin)

In [16]:
import folium
from folium.plugins import HeatMap
from IPython.display import display
import pandas as pd

category_colors = {
    'restaurant': 'orange',
    'attraction': 'purple',
    'accommodation': 'green',
    'point of interest': 'black',  
}

def create_map(city, df):
    
    if 'lat' not in df.columns or 'lng' not in df.columns:
        print(f"Error: Missing latitude or longitude data for {city}.")
        return None

    
    df = df.dropna(subset=['lat', 'lng', 'polarity'])

    
    df = df[df['polarity'] > 6].head(500)

    
    if df.empty:
        print(f"No valid data available for creating a map of {city} with the given conditions.")
        return None

    avg_lat = df['lat'].mean()
    avg_lon = df['lng'].mean()
    map_city = folium.Map(location=[avg_lat, avg_lon], zoom_start=13)

    heatmap_group = folium.FeatureGroup(name="Heatmap")
    # Used polarity as weight for heat map to adjust intensity
    heat_data = [[row['lat'], row['lng'], row['polarity']] for index, row in df.iterrows()]
    HeatMap(
        heat_data,
        radius=20,        
        blur=15,          
        min_opacity=0.3,  
        max_zoom=10,      
    ).add_to(heatmap_group)
    heatmap_group.add_to(map_city)

    marker_group = folium.FeatureGroup(name="Markers", show=True)
    for index, row in df.iterrows():
        marker_color = category_colors.get(row['category'].lower().strip(), 'black')
        
        folium.Marker(
            location=[row['lat'], row['lng']],
            popup=folium.Popup(
                html=(
                    f"<b>Name:</b> {row['name']}<br>"
                    f"<b>Category:</b> {row['category']}<br>"
                    f"<b>Address:</b> {row['address']}<br>"
                    f"<b>Number of Reviews:</b> {row['numReviews']}<br>"
                    f"<b>Polarity:</b> {row['polarity']}"
                ),
                max_width=300
            ),
            icon=folium.Icon(color=marker_color, icon='info-sign')
        ).add_to(marker_group)
    marker_group.add_to(map_city)
    folium.LayerControl(collapsed=False).add_to(map_city)
    
    legend_html = '''
     <div style="position: fixed; 
                 bottom: 180px; left: 50px; width: 250px; height: 200px; 
                 border:2px solid grey; z-index:9999; font-size:14px;
                 background-color:white; padding: 10px;">
     <b>Heatmap Intensity</b><br>
     <i style="background: blue; width: 20px; height: 20px; display: inline-block;"></i> Lower Polarity<br>
     <i style="background: lightblue; width: 20px; height: 20px; display: inline-block;"></i> Low Polarity<br>
     <i style="background: green; width: 20px; height: 20px; display: inline-block;"></i> Moderate Polarity<br>
     <i style="background: yellow; width: 20px; height: 20px; display: inline-block;"></i> High Polarity<br>
     <i style="background: orange; width: 20px; height: 20px; display: inline-block;"></i> Higher Polarity<br>
     <i style="background: red; width: 20px; height: 20px; display: inline-block;"></i> Highest Polarity<br>
     </div>
     '''
    map_city.get_root().html.add_child(folium.Element(legend_html))

    marker_legend_html = '''
     <div style="position: fixed; 
                 bottom: 20px; left: 50px; width: 250px; height: 150px; 
                 border:2px solid grey; z-index:9999; font-size:14px;
                 background-color:white; padding: 10px;">
     <b>Marker Colors</b><br>
     <i style="background: orange; width: 20px; height: 20px; display: inline-block;"></i> Restaurant<br>
     <i style="background: purple; width: 20px; height: 20px; display: inline-block;"></i> Attraction<br>
     <i style="background: green; width: 20px; height: 20px; display: inline-block;"></i> Accommodation<br>
     <i style="background: black; width: 20px; height: 20px; display: inline-block;"></i> Point of Interest<br>
     </div>
     '''
    map_city.get_root().html.add_child(folium.Element(marker_legend_html))

    # Comment out or not depending on if I want to display map in Jupyter
    display(map_city)

    # Saves map as html file
    map_city.save(f"{city}_singlecitymap.html")
    print(f"Map for {city} has been created and saved as {city}_singlecitymap.html.")
    return map_city

# Running function for only Berlin City data
city = "Berlin"
df_berlin = pd.DataFrame(data['Berlin'])
print(f"Creating and displaying map for {city} with the first 500 locations above a polarity of 6...")
if not df_berlin.empty:
    create_map(city, df_berlin)
else:
    print(f"No data available for {city}.")

Creating and displaying map for Berlin with the first 500 locations above a polarity of 6...


Map for Berlin has been created and saved as Berlin_singlecitymap.html.
